In [38]:
import numpy as np
import pandas as pd
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, Conv1D, GlobalMaxPooling1D, Dense
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score


In [39]:
df = pd.read_csv('/content/newdataset.csv')
texts = df['review'].values
labels = df['sentiment'].values

In [40]:
print(texts)
print(labels)

["One of the other reviewers has mentioned that after watching just 1 Oz episode you'll be hooked. They are right, as this is exactly what happened with me.The first thing that struck me about Oz was its brutality and unflinching scenes of violence, which set in right from the word GO. Trust me, this is not a show for the faint hearted or timid. This show pulls no punches with regards to drugs, sex or violence. Its is hardcore, in the classic use of the word.It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary. It focuses mainly on Emerald City, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. Em City is home to many..Aryans, Muslims, gangstas, Latinos, Christians, Italians, Irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.I would say the main appeal of the show is due to the fact that it goes where other shows w

In [41]:
maximum_features = 5000  # limit the no.of distinct word
maximum_length = 100 # all reviwes in same length (shorter= join as 0, longer= delete)
word_embedding_dims = 50 # [0.25, -0.11, 0.68, ..., 0.05]
no_of_filters = 250  #how many distinct features the model will learn to detect from the input data
kernel_size = 3  #take a 3 words at a time (like trigram)
hidden_dims = 250
batch_size = 16
epochs = 1
threshold = 0.5

In [42]:
tokenizer = Tokenizer(num_words=maximum_features)
print(tokenizer)
tokenizer.fit_on_texts(texts)
print("tokenizer:",tokenizer)
sequences = tokenizer.texts_to_sequences(texts)
print("sequences:",sequences)


tokenizer: <keras.src.legacy.preprocessing.text.Tokenizer object at 0x7ae27462ee60>
sequences: [[26, 4, 1, 81, 1906, 44, 944, 11, 98, 142, 38, 334, 2216, 427, 421, 25, 2506, 32, 22, 198, 13, 10, 6, 653, 46, 689, 15, 69, 1, 80, 151, 11, 2882, 69, 39, 2216, 12, 96, 3, 136, 4, 559, 58, 268, 7, 198, 34, 1, 550, 134, 1875, 69, 10, 6, 21, 2, 118, 16, 1, 1907, 37, 10, 118, 2344, 53, 15, 4231, 5, 1206, 403, 37, 559, 96, 6, 3330, 7, 1, 363, 341, 4, 1, 550, 8, 6, 419, 2216, 13, 11, 6, 1, 351, 5, 1, 4232, 2667, 1235, 8, 2812, 1236, 19, 568, 31, 3146, 4, 1, 1259, 114, 29, 1, 24, 3147, 3, 391, 33, 6, 21, 283, 19, 1, 568, 6, 325, 5, 110, 4795, 2507, 3, 51, 33, 355, 3, 22, 104, 229, 243, 9, 55, 130, 1, 280, 1350, 4, 1, 118, 6, 667, 5, 1, 193, 11, 8, 263, 114, 81, 272, 597, 2883, 760, 174, 1351, 4391, 16, 2732, 1151, 760, 1544, 760, 773, 2216, 147, 931, 178, 1, 80, 427, 9, 123, 222, 2882, 69, 13, 33, 1498, 8, 12, 2300, 9, 422, 130, 9, 12, 1530, 16, 8, 17, 13, 9, 273, 51, 9, 1451, 2, 1325, 16, 2216, 3,

In [43]:
x_data = pad_sequences(sequences, maxlen=maximum_length)
print(x_data)
x_train, x_test, y_train, y_test = train_test_split(x_data, labels, test_size=0.2, random_state=42) 

[[ 178    1   80 ...  117 4233  520]
 [  27   44   29 ... 2217   66  217]
 [  10    6   21 ...   61   15  401]
 ...
 [  11 1961  212 ...   64    2  546]
 [   6  174  156 ...    5  361    8]
 [  78    1  416 ...  926    4 4210]]


In [44]:
label_mapping = {'negative': 0, 'positive': 1}
y_train = np.array([label_mapping[label] for label in y_train])
y_test = np.array([label_mapping[label] for label in y_test])

print("y_train:",y_train)
print("y_test:",y_test)

y_train: [1 0 0 ... 1 0 1]
y_test: [1 0 0 0 1 1 0 1 0 0 0 1 1 0 1 1 0 1 0 0 1 0 0 1 1 1 1 1 1 0 1 1 1 1 0 0 0
 1 0 0 1 0 0 1 1 1 0 0 0 1 1 1 1 1 1 1 0 0 0 0 1 0 0 1 0 1 0 1 1 0 1 0 1 1
 1 0 0 1 0 1 1 1 1 0 1 1 0 1 1 1 0 1 1 1 1 0 1 1 0 1 0 0 1 1 0 0 1 0 0 0 0
 1 0 0 0 1 1 0 0 1 0 1 1 1 0 0 1 0 1 0 1 0 1 1 0 0 1 1 1 0 0 1 0 0 0 1 1 0
 0 1 1 1 0 1 1 0 1 0 0 1 1 0 0 0 0 1 1 1 1 1 1 0 1 0 1 0 0 0 1 1 1 1 0 0 1
 1 1 1 0 1 0 1 1 0 0 1 1 1 0 1 1 0 0 1 0 0 1 0 0 1 0 1 1 1 0 0 1 1 1 0 1 1
 1 0 1 0 0 1 0 1 0 0 0 0 0 0 0 1 0 1 1 1 0 1 1 0 1 0 1 0 0 0 0 1 0 0 1 0 1
 1 0 1 1 0 1 1 0 1 0 1 0 0 0 1 1 1 0 1 1 1 1 1 1 1 1 1 0 0 1 1 1 1 1 0 1 0
 1 1 1 1 0 0 0 1 0 1 0 0 1 0 0 1 1 0 1 1 1 0 1 0 0 0 1 1 1 1 0 0 0 1 0 0 1
 0 0 0 0 0 1 0 0 1 1 0 0 1 0 0 0 1 1 0 1 0 1 0 1 1 0 1 0 0 0 1 1 1 1 0 1 0
 0 0 1 1 1 0 0 0 0 1 0 1 0 1 1 0 0 1 0 1 1 1 0 0 0 1 0 0 0 1 1 1 0 1 0 1 0
 1 0 1 1 0 1 0 1 1 1 1 0 1 0 0 0 0 0 0 1 0 1 1 1 1 1 0 0 0 1 1 1 1 1 0 1 0
 0 1 1 1 1 1 0 1 1 1 1 0 0 1 1 0 1 0 1 0 1 0 0 1 1 1 1 0 0 1 1 1 

In [45]:
x_train = np.array(x_train)
y_train = y_train.astype(np.int32)
x_test = np.array(x_test)
y_test = y_test.astype(np.int32)

In [46]:
model = Sequential()
model.add(Embedding(maximum_features, word_embedding_dims, input_length=maximum_length))
model.add(Conv1D(no_of_filters, kernel_size, padding='valid', activation='relu', strides=1))
model.add(GlobalMaxPooling1D())
model.add(Dense(hidden_dims, activation='relu'))
model.add(Dense(1, activation='sigmoid'))


model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
model.fit(x_train, y_train, batch_size=batch_size, epochs=epochs, validation_data=(x_test, y_test))

# model.add(Embedding(input_dim, output_dim=3, input_length=3))  

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


238/238 ━━━━━━━━━━━━━━━━━━━━ 3s 5ms/step - accuracy: 0.5516 - loss: 0.6738 - val_accuracy: 0.7513 - val_loss: 0.4965


In [47]:
y_pred_prob = model.predict(x_test)
y_pred = (y_pred_prob > threshold).astype(int)

30/30 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step


In [48]:
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)

print('Accuracy:', accuracy)
print('Precision:', precision)
print('Recall:', recall)
print('F1-score:', f1)

Accuracy: 0.751311647429171
Precision: 0.7650862068965517
Recall: 0.7349896480331263
F1-score: 0.7497360084477297


In [ ]:
new_sentence = "The movie was fantastic and very enjoyable"
new_sequence = tokenizer.texts_to_sequences([new_sentence])
new_padded_sequence = pad_sequences(new_sequence, maxlen=maximum_length)

new_pred_prob = model.predict(new_padded_sequence)
new_pred = (new_pred_prob > threshold).astype(int)

predicted_label = 'positive' if new_pred[0] == 1 else 'negative'

print("New sentence:", new_sentence)
print("Predicted sentiment:", predicted_label)


In [ ]:
#Accuracy  = correct classification/total classification
